# L3 Analyse Numérique – TP3

[Dequay A](mailto:antoine.dequay@ens-rennes.fr) &
[Le Barbenchon P](mailto:pierre.le-barbenchon@ens-rennes.fr). TP ENS Rennes

[Boutin B](mailto:benjamin.boutin@univ-rennes1.fr). Cours et TP Université de Rennes 1 - UFR Mathématiques  

Ce TP a pour objet les méthodes directes et itératives pour résoudre $Ax=b$.

Ainsi dans tout ce TP, on n'utilisera jamais la commande $\verb"np.linalg.solve"$ pour résoudre les systèmes linéaires.

- Exercice 1. Résolution de systèmes triangulaires
- Exercice 2. Algorithme de décomposition LU
- Exercice 3. Comparaison des méthodes de Jacobi, Gauss-Seidel et de relaxation.
- Exercice 4. Résolution d'un problème de Poisson 2D

Nous importons avant tout quelques librairies qui seront utiles.

In [2]:
from math import *
import numpy as np
import matplotlib.pyplot as plt

## Exercice 1. Résolution de systèmes triangulaires

<b>Théorème (Décompostion LU)</b> Soit $A\in\mathcal{M}_n(\mathbb{K})$, dont tous les mineurs principaux sont non nuls, c'est-à-dire que pour tout $k\in\{1,\ldots,n\}$ la sous-matrice extraite $(A_{i,j})_{1\leq i,j\leq k}$ est inversible.

Alors il existe un unique couple $(L,U)$ de matrices carrées d'ordre $n$ tel que :
- $L$ est triangulaire inférieure avec uniquement des 1 sur la diagonale;
- $U$ est triangulaire supérieure avec des coefficients diagonaux tous non nuls;
- $A=LU$.

Une fois cette décomposition connue, la résolution d'un système linéaire $Ax=b$ est équivalente à la résolution de deux systèmes linéaires triangulaires, élémentaires à résoudre :
$$
(Ax=b) \Longleftrightarrow (Ly=b\textrm{ et }Ux=y).
$$

### Question 1)

Programmer l'algorithme ```Lower(L,b)``` premettant de résoudre des systèmes triangulaires inférieurs ($Ly=b$).

### Question 2)

Tester cet algorithme sur une matrice $M$ telle que $M_{i,j} = 1+i+j$ pour tous $0 \leq i < j \leq n-1$, et $M_{i,i} = 1$ et pour des $b$ aléatoires.

### Question 3) 

Programmer l'algorithme ```Upper(U,b)``` premettant de résoudre des systèmes triangulaires supérieurs ($Uy=b$).

## Exercice 2. Algorithme de décomposition LU

L'algorithme de construction des matrices $L$ et $U$ s'appuie sur les opérations d'élimination du pivot de Gauss.
Pour réduire de moitié la complexité en espace (<b>forme compacte</b>), l'algorithme agit directement sur la matrice $A$, la matrice $U$ étant construite au fil des itérations dans la partie supérieure de $A$, et la matrice $L$ correspondant aux opérations du pivot étant stockée dans la partie inférieure de $A$. On a ainsi à l'issue de l'algorithme $U_{i,j}=A_{i,j}$ si $i\leq j$, et $L_{i,j}=A_{i,j}$ si $i>j$, les autres coefficients de $L$ et $U$ étant nuls ou égaux à 1.


\begin{align*}
&\textbf{Algorithme de la factorisation LU.}\\
&\textbf{Forme compacte}\\
&\text{Pour }k=1,\ldots,n-1\\
&\phantom{.}\hspace{2em}\text{Pour } i=k+1,\ldots, n\\
&\phantom{.}\hspace{4em}A_{i,k}\leftarrow A_{i,k}/A_{k,k}\\
&\phantom{.}\hspace{4em}\text{Pour } j=k+1,\ldots,n\\
&\phantom{.}\hspace{6em}A_{i,j}\leftarrow A_{i,j}-A_{i,k}A_{k,j}\\
&\phantom{.}\hspace{4em}\text{Fin pour } j\\
&\phantom{.}\hspace{2em}\text{Fin pour }i\\
&\text{Fin pour }k.
\end{align*}

Attention ! Quand on définit un ```np.array``` avec des valeurs entières, Python ne fait des opérations que dans les entiers. Ainsi pour la matrice $A = \begin{pmatrix} 14 & 4 \\ 5 & 7 \end{pmatrix}$, l'algorithme renverra la matrice $\begin{pmatrix} 14 & 4 \\ 0 & 7 \end{pmatrix}$, alors que la vraie décomposition compacte LU est $\begin{pmatrix} 14 & 4 \\ \frac{5}{14} & \frac{39}{7} \end{pmatrix}$. Pour palier ce problème d'opérations faites dans le monde des entiers, il faut, en définissant la matrice $A$ :
- soit mettre des flottants : ```A = np.array([[14.,4.],[5.,7.]])```
- soit dire qu'on manipule des flottants : ```A = np.array([[14,4],[5,7]], dtype = 'float64')```

### Question 1)

Programmer cet algorithme (on essayera si possible d'obtenir une programmation concise, idéalement avec seulement une boucle sur $k$)

### Question 2)

Programmer une fonction ```Pascal(n)``` renvoyant la matrice de Pascal. Par exemple la matrice de Pascal de dimension 5 est la suivante 
$$
P = \begin{pmatrix}
1 & 1 & 1 & 1 & 1\\
1 & 2 & 3 & 4 & 5\\
1 & 3 & 6 & 10 & 15\\
1 & 4 & 10 & 20 & 35\\
1 & 5 & 15 & 35 & 70
\end{pmatrix}.
$$

### Question 3)

Tester la décomposition LU sur la matrice de Pascal pour plusieurs $n$.

## Exercice 3. Comparaison des méthodes de Jacobi, Gauss-Seidel et de relaxation

Le but de la suite de ce TP est d'introduire et de comparer quelques méthodes itératives pour résoudre le système $Ax=b$.

<b>Principe :</b> La matrice $A$ est décomposée sous la forme $A=M-N$ avec $M$ facile et peu coûteuse à inverser et la solution $x$ est approchée par une suite $(x_k)_{k\in\mathbb N}$ d'éléments de $\mathbb R^n$:
$$\begin{align*} 
x_{0} &\in \mathbb R^n,\\
Mx_{k+1} &= Nx_{k}+b.
\end{align*}$$
La matrice $M^{-1}N$ est fondamentale dans l'analyse de convergence. En effet la solution $x$ est l'unique point fixe d'une application affine sur $\mathbb R^n$ dont la différentielle (constante) a pour matrice $M^{-1}N$. En particulier la convergence itérative de la méthode, requise pour tout choix de l'initialisation $x_0$, est équivalente à la condition suivante sur le rayon spectral:
$$\rho(M^{-1}N)<1.$$

Quelques possibilités pour construire $M$ et $N$ : écrivons $A=D-E-F$ avec $D$ la partie diagonale de $A$, $-E$ sa partie triangulaire inférieure stricte et $-F$ sa partie triangulaire supérieure stricte. Autrement dit
$$
\begin{aligned}
D_{ii}&=A_{ii} && i=1,\ldots,n,\\
E_{ij}&=-A_{ij} && 1\leq j<i\leq n,\\
F_{ij}&=-A_{ij} && 1\leq i<j\leq n,
\end{aligned}
$$
tous les autres termes étant nuls. Pour la construction de ces trois parties utilisera la commande ```np.diag```.


- Méthode de Jacobi : $M=D$ et $N=E+F$.
- Méthode de Gauss-Seidel : $M=D-E$ et $N=F$.
- Méthode de relaxation : $M=\frac 1\omega D-E$ et $N=\frac{1-\omega}\omega D+F$ avec $\omega\in\mathbb R^+_{*}$.





Soit la matrice carrée $A$ de taille $n$, tridiagonale, intervenant dans le TP précédent, définie par
$$
  A = 
  \begin{bmatrix}
    2 & -1 &  0 & \ldots & 0 \\
    -1 & 2 & -1 &  \ddots & \vdots  \\
    0  & \ddots & \ddots & \ddots & 0 \\
    \vdots & \ddots & -1 & 2 & -1 \\
    0 & \ldots & 0 & -1 & 2
  \end{bmatrix}
$$


### Question 1)

Programmer les trois méthodes précedentes.

### Question 2)


Application : utiliser ces trois méthodes sur la matrice $A$ et le second
  membre $B = (1,0,\ldots,0,1)^T$, pour
  $n=10$. On effectuera 100 itérations. Dans le cas de la méthode de relaxation,
  on choisira $\omega = \tfrac{3}{2}$.



### Question 3)


Dans le cas où $n=20$, déterminer le paramètre optimal dans la méthode de 
  relaxation, en représentant le rayon spectral de la matrice d'itération obtenue en
  fonction de $\omega$.



### Question 4)

 Pour différentes valeurs de $n$, comparer le nombre d'itérations
  nécessaires pour avoir une précision de $10^{-12}$ entre la solution
  approchée et la solution exacte. Quelle relation y a t-il entre le nombre
  d'itérations et le rayon spectral ?

 ### Question 5) 
Vérifier que la méthode de Jacobi appliquée à la matrice 
$$
    C =
    \begin{bmatrix}
      1 & 2 & -2 \\
      1 & 1 & 1 \\
      2 & 2 & 1 \\
     \end{bmatrix}
$$
converge, mais que la méthode de Gauss-Seidel diverge.

### Question 6)
Vérifier que la méthode de Gauss-Seidel appliquée à la matrice 
$$
    D =
    \begin{bmatrix}
      2 & -1 & 1 \\
      2 & 2 & 2 \\
      -1 & -1 & 2 \\
     \end{bmatrix}
$$
  converge, mais que la méthode de Jacobi diverge.

## Exercice 4. Résolution d'un problème de Poisson 2D

On souhaite résoudre le problème de Poisson en dimension 2 d'espace
$$
\dfrac{\partial^2 u}{\partial x^2} + \dfrac{\partial^2 u}{\partial y^2} = f(x,y), \quad (x,y)\in[0,1]^2,
$$
assorti des conditions de Dirichlet au bord 
$$ u(x,y)=0,\quad (x,y)\in\partial [0,1]^2.$$

Pour ce faire, on approche l'équation par différences finies. Soit $N$ un entier naturel, on pose $h=1/(N+1)$ le pas de discrétisation pour chacune des directions. Pour tout $0\leq i,j\leq N+1$, $u_{i,j}$ désigne une approximation de la valeur $u(x_i,y_j)$, les points de la grille étant $x_i= i h$, $y_j = jh$.
L'EDP est approchée par des différences centrées :
$$
\dfrac{u_{i+1,j}-2u_{i,j}+u_{i-1,j}}{h^2} + \dfrac{u_{i,j+1}-2u_{i,j}+u_{i,j-1}}{h^2} = f(x_i,y_j), \quad 1\leq i,j \leq N,
$$
et les conditions de bord sont données: $u_{i,j}=0$ lorsque $ij(N+1-i)(N+1-j)=0$.




### Question 1)

 Construire la matrice $A$ de taille $N^2\times N^2$ permettant de définir le vecteur des inconnues $U=(u_{i,j})_{1\leq i,j\leq N}$ de $\mathbb R^{N\times N}$ comme solution du problème
$$AU = F.$$



### Question 2) 
En utilisant les méthodes itératives précédemment mises en œuvre, résoudre ce problème pour le second membre $f$ donné dans l'exemple de code ci-dessous.


### Question 3)
Représenter la solution. On pourra adapter l'exemple suivant pour tracer une surface en 3 dimensions :
```python
from mpl_toolkits.mplot3d import axes3d
from matplotlib import cm

fig = plt.figure()
ax = fig.gca(projection = '3d')
n = 20
X = np.linspace(0,1,n+2)
Y = X
X, Y = np.meshgrid(X, Y)
def f(x,y):
    return -(x-0.5)**2 - (y-0.5)**2
Z = f(X,Y)
surf = ax.plot_surface(X, Y, Z,cmap = cm.coolwarm,linewidth = 0, 
    		antialiased = False)
plt.title("La surface f(x,y)=-(x-0.5)**2-(y-0.5)**2")
plt.show()
```

où ```X``` et ```Y``` sont les vecteurs avec les coordonnées des points du plan, et ```Z``` est la matrice contenant les valeurs ```f(X,Y)```.
